In [2]:
import spacy
from spacy import displacy
from collections import Counter
import en_core_web_sm
#!pip install https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-2.2.0/en_core_web_sm-2.2.0.tar.gz --user
nlp = en_core_web_sm.load()
import pandas as pd
import json
!pip install bs4 --user
from bs4 import BeautifulSoup
import requests
import re
import os
import mmap
import random
from spacy.gold import GoldParse
from spacy.scorer import Scorer
from spacy.util import minibatch, compounding

You are using pip version 18.0, however version 19.3.1 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


## Load data

In [4]:
with open('data.json', 'r') as f:
    dict_json_weighted = json.load(f)
object_1 = list(dict_json_weighted.keys())[2]
for i in range(len(dict_json_weighted[object_1]['log'])):
    print(str(i)+"-"+dict_json_weighted[object_1]['log'][i]['text'])

0-Can I get some information on a train?
1-Yes. Is there something specific you are looking for?
2-I'd like a train to depart at 9:30 in Cambridge.
3-i recommend TR1006.  it goes to london kings cross and costs 19. 51. can we book?
4-how long is that train ride?
5-It is 51 minutes. Would you like me to make a booking for you?
6-No but I do need help finding a particular hotel called the Gonville HOtel.
7-Gonville Hotel is an expensive 3 star hotel in the centre of town with free internet and parking. Would you like more information or to book it?
8-I'd like to book it. Can you book it starting Sunday night for 5 nights. I need reservations for 6 people.
9-Ok, booking was successful! Your reference number is 5X759ZBR. Is there anything else I can help you with today?
10-You took care of everything, thank you so much.
11-You are very welcome.


## Load ontology

In [5]:
with open('ontology.json', 'r') as o:
    ontology = json.load(o)
    my_ent=list(ontology.keys())
    
    
action=['inform', 'request', 'select', 'recommend', 'not found', 'request booking', 'offer booking', 
        'inform booked', 'decline booking', 'welcome','greet', 'bye', 'reqmore' ]
topic= ['hotel', 'restaurant', 'taxi', 'train', 'attraction', 'police', 'hospital']

## display topics and actions

In [6]:
top=[]
act=[]
ont=list(ontology.keys())
for i in range(len(dict_json_weighted[object_1]['log'])):
    #print(dict_json_weighted[object_1]['log'][i]['text'])
    sentence =nlp (dict_json_weighted[object_1]['log'][i]['text'])
    for x in [y for y in sentence if y.pos_ != 'PUNCT']:
        if str(x).lower() in topic:
            if str(x).lower() not in top:
                top.append(str(x).lower()) 
        if x.lemma_ in action:
            if x.lemma_ not in act:
                act.append(x.lemma_)
        #for z in ont:
            #if str(x) in str(ontology[z]):
                #print(z+" :"+str(x))           
print("topics: "+str(top))
print("actions: "+str(act))


topics: ['train', 'hotel']
actions: ['recommend', 'welcome']


## Display the updated slots 

In [7]:
for i in dict_json_weighted[object_1]['goal']:
    if i not in['message', 'topic']:
        if dict_json_weighted[object_1]['goal'][i] !={}:
            print("****** "+i+" ******")
            for j in (dict_json_weighted[object_1]['goal'][i]):
                if dict_json_weighted[object_1]['goal'][i][j] not in ['fail_info', {}]:
                    print("°"+j)
                    print(dict_json_weighted[object_1]['goal'][i][j])
    

****** hotel ******
°book
{'invalid': True, 'stay': '5', 'day': 'sunday', 'people': '6'}
°info
{'name': 'gonville hotel'}
°fail_info
{'name': 'limehouse'}
****** train ******
°info
{'departure': 'cambridge', 'leaveAt': '09:30', 'destination': 'peterborough', 'day': 'friday'}
°reqt
['trainID', 'price', 'duration']


# Custom NER

### create training sample

In [2]:
Train_data = [
   (
        "Hello, I am looking for a cheap place to dine in the centre", { "entities" :
        [(26, 45, "restaurant-price-range"), (46, 59, "restaurant-area")]
        }
    ),(
        "not really but i need it for 3 people",  { "entities" : 
        [(25, 37, "restaurant-book-people")]
        }
    ),(
        "I recommend La Raza - fantastic (and cheap!) Spanish cuisine. I'd be happy to book a table for you, if you like.",  { "entities" : 
        [(12, 20, "restaurant-name"), (37, 42, "restaurant-price-range"),(45, 60, "restaurant-food")]
        }

    ),(
        "Yes for 3 at 14:45 wednesday, can I get the reference number too please", 
        { "entities" :
        [(4, 9, "restaurant-book-people"), (10, 18, "restaurant-book-time"), (19, 28, "restaurant-book-day")]
        }
    ),( 
        "Both offer free parking and free wifi. The Alexander B&B is 4 star rated. The El Shaddai has a 0 rating.", { "entities" : 
             [(11, 23, "hotel-parking"), (28, 37, "hotel-internet"), (39, 56, "hotel-name"), (60, 66, "hotel-stars"), (74, 87, "hotel-name"), (95, 103, "hotel-stars")]
             }
    ),( 
        "3 nights, 3 people, please.", { "entities" : 
             [(0, 8, "hotel-book-stay"), (10, 18, "hotel-book-people")]
             }
    ),( 
        "I would like a taxi from the hotel to the restaurant. I would like to arrive by 14:45. I would like the contact number and car type",  { "entities" : 
             [(77, 85, "taxi-arrive-by")]
             }
    ),( 
        "Thanks. I also need a cheap place to stay in the center.", { "entities" : 
             [(22, 33, "hotel-price-range"),(42, 55, "hotel-area")]
             }
    ),( 
        "I am looking for info about a hotel called city centre north b and b. Can you help?", { "entities" : 
             [(43, 68, "hotel-name")]
             }
    ),( 
        "Yes. City Centre North B and B is a guesthouse in the north side of town, that has both free internet and parking. Do you want to book a room?", { "entities" : 
             [(5,30, "hotel-name"),(34, 46, "hotel-type"),(47, 72, "hotel-area")]
             }
    ),( 
        "Ok, I am also looking for a train from Cambridge to Bishops Stortford.", { "entities" : 
             [(34, 48, "train-departure"),(49, 69, "train-destination")]
             }
    ),( 
        "I'll be leaving Monday after 15:30.", { "entities" : 
             [(16, 22, "train-day"),(23, 34, "train-leave-at")]
             }
    ),( 
        "TR2630 leaves at 17:29. Would you like for me to book the train for you?", { "entities" : 
             [(14, 22, "train-leave-at")]
             }
    ),( 
        "Yes I would like to book the train for 4 people and I'll need the reference number please.", { "entities" : 
             [(35, 47, "train-book-people")]
             }
    ),( 
        "I'm looking for a Mediterranean restaurant near the centre of town.", { "entities" : 
             [(18, 42, "restaurant-food"), (43, 66, "restaurant-area")]
             }
    ),( 
        "I've got three that fit that bill... the gardenia, la mimosa, and shiraz.  Do you have a preference?", { "entities" : 
             [(37, 49, "restaurant-name"),(51, 60, "restaurant-name"),(65, 72, "restaurant-name")]
             }
    ),( 
        "Great, could I book a table of 5 for 11:30 on wednesday? If so, please provide me with a reference number", { "entities" : 
             [(20, 32, "restaurant-book-people"),(33, 42, "restaurant-book-time"),(43, 55, "restaurant-bookday")]
             }
    ),( 
        "Is one of them in the cheap price range? ", { "entities" : 
             [(15, 39, "restaurant-price-range")]
             }
    ),( 
        "Yes. Can you please search for an attraction in the type of college?", { "entities" : 
             [(45, 67, "attraction-type")]
             }
    ),( 
        "Is an entrance fee okay? If so, the corpus christi college located at king's parade. Fee is 2 pounds. Would you like the phone number? ", { "entities" : 
             [(32, 58, "attraction-name")]
             }
    ),( 
        "I would like to leave Corpus Christi College in enough time to arrive at the restaurant at the booked time of 11:30. ", { "entities" : 
             [(22, 44, "train-departure"), (88, 130, "train-arrive-by")]
             }
    ),( 
        "I'm looking for a place to stay in Cambridge. It should include free wifi and be a 3 star.  Can you help me please? ", { "entities" : 
             [(64, 73, "hotel-internet"), (78, 89, "hotel-stars")]
             }
    ),( 
        "There are five to choose from. Would you like moderate or expensive price point? ", { "entities" : 
             [(46, 67, "hotel-price-range")]
             }
    ),( 
        "I have the gonville hotel. It is expensive. Would you like me to book that for you?", { "entities" : 
             [(7, 25, "hotel-name"), (33, 42, "hotel-price-range")]
             }
    ),( 
        "Do they have free parking? If so, please reserve a room for Tuesday for 7 people, 4 nights.", { "entities" : 
             [(13, 25, "hotel-parking"), (56, 67, "hotel-book-day"), (68, 80, "hotel-book-people"), (81,89, "hotel-book-stay")]
             }
    ),( 
        "I am looking for a hotel called The Cambridge Belfry. Can you help me with this? ", { "entities" : 
             [(32, 45, "hotel-name")]
             }
    ),( 
        "Yes, thank you. I'd also like to find a swimming pool in the town centre. ", { "entities" : 
             [(40, 53, "attraction-type"), (57, 75, "attraction-area")]
             }
    ),( 
        "Yes, can you please help me book a taxi to leave the hotel by 03:15", { "entities" : 
             [(59, 69, "taxi-leave-at")]
             }
    ),( 
        "I am looking for a restaurant in the moderate price range that serves Indian food", { "entities" : 
             [(30, 57, "restaurant-price-range"), (70, 81, "restaurant-food")]
             }
    ),( 
        "Curry prince is an indian restaurant, in the moderate price range and in the east.", { "entities" : 
             [(0, 12, "restaurant-name"), (13, 36, "restaurant-food"), (38, 65, "restaurant-price-range" ), (70, 81,"restaurant-area") ]
             }
    ),( 
        "Rajmahal is an Indian restaurant in the east part of town and in the moderate price range. ", { "entities" : 
             [(15, 32, "restaurant-food"), (33, 57, "restaurant-area"), (62, 89, "restaurant-price-range")]
             }
    ),( 
        "I want a train that leaves on Monday", { "entities" : 
             [(30, 36, "train-day")]
             }
    ),( 
        "I would like to travel from Norwich to Cambridge. Are there any leaving after 21:00? ", { "entities" : 
             [(23, 36, "train-departure"), (36,48, "train-destination"), (72,83, "train-leave-at")]
             }
    ),( 
        "it should arrive by 22:35 ", { "entities" : 
             [(17, 25, "train-arrive-by")]
             }
    ),( 
        "No thanks but could you help me find a good college to visit on the south side of town? ", { "entities" : 
             [(44, 51, "attraction-type"), (61,86,"attraction-area")]
             }
    ),( 
        "How about a theater in the south? ", { "entities" : 
             [(10, 18, "attraction-type"), (20, 32, "attraction-area")]
             }
    ),( 
        "The junction theatre is the only one that meets your specified critera. ", { "entities" : 
             [(0, 21, "attraction-name")]
             }
    ),( 
        "I'm looking for architecture in the centre part of town. Can you help me with that? ", { "entities" : 
             [(16, 29, "attraction-type"), (29, 55, "attraction-area")]
             }
    ),( 
        "I personally like Little Saint Mary's Church on Little Saint Mary's Lane.  Admission is free.", { "entities" : 
             [(18, 45, "attraction-name")]
             }
    ),( 
        "Are there any trains going to Cambridge on Friday? ", { "entities" : 
             [(27, 39, "train-departure"), (40,49, "train-day")]
             }
    ),( 
        "I will be departing from London Kings Cross after 20:45", { "entities" : 
             [(20, 43, "train-departure"), (44,55,"train-leave-at")]
             }
    ),( 
        "There is a 21:17 that will arrive by 22:08.", { "entities" : 
             [(11, 17, "train-leave-at"), (27, 42, "train-arrive-by")]
             }
    ),( 
        "I am looking for a guesthouse to stay at with free wifi please.", { "entities" : 
             [(17, 29, "hotel-type"), (46, 55, "hotel-internet")]
             }
    ),( 
        "I don't care about the price range, either, as long as it is a 4 star guesthouse with free wifi.", { "entities" : 
             [(63, 69, "hotel-stars"), (70, 80, "hotel-type"), (86, 95, "hotel-parking")]
             }
    ),( 
        "No it will be for 2 people for 5 nights.", { "entities" : 
             [(18, 26, "hotel-book-people"), (27, 39,"hotel-book-stay")]
             }
    ),( 
        "Yes! Wandlebury country park is located in south and the entrance fee is free. ", { "entities" : 
             [(5, 29, "attraction-name"), (40, 49, "attraction-area")]
             }
    ),( 
        "We don't have any multiple sports facilities in the centre of town. Do you want to look for something else?", { "entities" : 
             [(18, 34, "attraction-type"), (45, 59, "attraction-area")]
             }
    ),( 
        "Darrys Cookhouse and Wine Shop is a modern European restaurant located in the centre of town.  It's in the expensive price range.  Would you like to make a reservation? ", { "entities" : 
             [(0, 30, "restaurant-name"), (36, 51, "restaurant-food"),(71,84, "restaurant-area"), (107,116, "restaurant-price-range")]
             }
    ),( 
        "Yes, that would be great. I'll need a table for 7 on Friday at 18:00. ", { "entities" : 
             [(36, 49, "restaurant-book-people"), (50, 59, "restaurant-book-day"), (60,69, "restaurant-book-time")]
             }
    ),( 
        "Yes, I would like it to be in the north.", { "entities" : 
             [(27,39,"hotel-area")]
             }
    ),( 
        "Okay, I would like to recommend the Acorn Guest House.", { "entities" : 
             [(32,41,"hotel-name"),(42,53,"hotel-type")]
             }
    ),( 
        "Please book it for 2 people for 2 nights starting on wednesday, and provide the reference number.  Also, we would like to find an attraction near the hotel.", { "entities" : 
             [(15,28,"hotel-book-people"),(32,40,"hotel-book-stay"),(50,62,"hotel-book-day"),(140,155,"attraction-area")]
             }
    ),( 
        "Okay. There are boats, a park, and pools. Would like more information on any of this? ", { "entities" : 
             [(16,21,"attraction-type"),(23,29,"attraction-type"),(35,40,"attraction-type")]
             }
    ),( 
        "I would recommend riverboat georgina. Would you like the address or phone number for that? ", { "entities" : 
             [(18,35,"attraction-name")]
             }
    ),( 
        "I would like to go this Saturday to Cambridge.", { "entities" : 
             [(24,32,"train-day"),(33,45,"train-destination")]
             }
    ),( 
        "TR4300 will arrive at birmingham new street by 8:44. Would you like to book a ticket?", { "entities" : 
             [(19,43,"train-destination"),(44,51,"train-arrive-by")]
             }
    ),( 
        "A train from Cambridge to Birmingham New Street on Monday will cost 75.10 pounds.", { "entities" : 
             [(8,22,"train-departure"),(23,47,"train-destination"),(48,58,"train-day")]
             }
    ),( 
        "I'll be leaving from Cambridge on Tuesday. I'd like to get to Leicester by 18:00 please. ", { "entities" : 
             [(16,30,"train-departure"),(31,41,"train-day"),(59,71,"train-destination"),(72,80,"train-arrive-by")]
             }
    ),( 
        "I would like to book a taxi to the gandhi. ", { "entities" : 
             [(28,41,"taxi-destination")]
             }
    ),( 
        "Hi, I need to get in from King's Lynn to Cambridge ", { "entities" : 
             [(21,37,"train-departure"),(38,50,"train-destination")]
             }
    ),( 
        "How about a museum in the centre? ", { "entities" : 
             [(12,18,"attraction-type"),(19,32,"attraction-area")]
             }
    ),( 
        "Yes I am looking for architecture and will need the address, postcode and phone number of the attraction. ", { "entities" : 
             [(21,33,"attraction-type")]
             }
    ),( 
        "How about the holy trinity church? ", { "entities" : 
             [(10,33,"attraction-name")]
             }
    ),( 
        "There are 3 choices, 2 moderately priced and 1 expensive. Do you have a preference? ", { "entities" : 
             [(23,40,"restaurant-price-range"),(47,56,"restaurant-price-range")]
             }
    ),( 
        "I need the address and phone number of a restaurant in the center of town that serves Turkish food. Thanks. ", { "entities" : 
             [(52,73,"restaurant-area"),(86,98,"restaurant-food")]
             }
    ),( 
        "I can suggest Pizza Hut in Fen Ditton located in Cambridge Retail Park Newmarket. ", { "entities" : 
             [(14,23,"restaurant-name"),(46,80,"restaurant-area")]
             }
    ),( 
        "Yes, could you book me 2 tickets and get me a reference number? ", { "entities" : 
             [(23,32,"train-book-people")]
             }
    ),( 
        "You'll be in a white Skoda and the contact number is 07935 536 503. Can I confirm, though, that you wish to leave the restaurant at 5:15 in the morning? ", { "entities" : 
             [(108,128,"taxi-departure"),(129,136,"taxi-leave-at")]
             }
    ),( 
        "I want to leave on Saturday at any time after 21:15. ", { "entities" : 
             [(16,27,"train-day"),(40,51,"train-leave-at")]
             }
    ),( 
        "There are 13 colleges in the centre.  King's College and Saint Catharine's College are on the same street and both have free admission.", { "entities" : 
             [(13,21,"attraction-type"),(22,35,"attraction-area"),(38,52,"attraction-name"),(57,82,"attraction-name")]
             }
    ),( 
        "the whipple museum of the history of science is an interesting one! ", { "entities" : 
             [(0,19,"attraction-name")]
             }
    ),( 
        "Actually yes! TR5975 leaves from broxbourne at 21:01. It's 14.32 pounds. Does that work? ", { "entities" : 
             [(28,43,"train-departure"),(44,52,"train-leave-at")]
             }
    ),( 
        "Yes. Downing college is free and the phone number is 01223334860. ", { "entities" : 
             [(5,20,"attraction-name")]
             }
    ),( 
        "I am going to Cambridge and i plan to depart from stansted airport and i need a train schedule from stansted airport that will get to Cambridge by 13:30 Tuesday. ", { "entities" : 
             [(11,23,"train-destination"),(45,66,"train-departure")]
             }
    ),( 
        "The allenbell is a guesthouse located in the east. It is a cheap 4 star hotel with free parking and internet. ", { "entities" : 
             [(0,13,"hotel-name"),(19,29, "hotel-type"), (38,49, "hotel-area"), (59,63,"hotel-price-range"), (65,71,"hotel-stars"),(83,95,"hotel-parking")]
             }
    ),
]



##### generate only from training set

In [13]:
result1= open("FinalData/chatito/chatito_datatrain.txt","w+")
result2= open("FinalData/chatette/chatette_datatrain.txt","w+")
r1 = open("FinalData/chatito/chatito_datatrain.txt", "r+")  
r2 = open("FinalData/chatette/chatette_datatrain.txt", "r+")
r1.write("\n")
r2.write("\n")
x=""
y=""
for text, annotations in Train_data:
    
    for ent in annotations.get('entities'):
        #print(ent[2])
        x=ent[0]
        y=ent[1]
        #print(text[x:y])

        r1 = open("FinalData/chatito/chatito_datatrain.txt", "r+")  
        r2 = open("FinalData/chatette/chatette_datatrain.txt", "r+")

                #using chatette format
        if ent[2] in r2.read():
            r2.write("|"+text[x:y])
        else:
            r2.write("\n")
            r2.write("\n")
            r2.write(" ~["+ent[2]+"]\n")
            r2.write("    "+text[x:y])
                 #using chatito format
        if ent[2] in r1.read():
            r1.write("    "+text[x:y]+"\n")
        else: 
            r1.write("\n")
            r1.write("\n")
            r1.write("~["+ent[2]+"]\n")
            r1.write("    "+text[x:y]+"\n")

### Training

In [9]:
new_model=""
output_dir2 = ("output_dir2")
def main_train(model=None, output_dir=r'model', n_iter=100):
    """Load the model, set up the pipeline and train the entity recognizer."""
    if model is not None:
        nlp = spacy.load(model)  # load existing spaCy model
        print("Loaded model '%s'" % model)
    else:
        nlp = spacy.blank("en")  # create blank Language class
        print("Created blank 'en' model")

    # create the built-in pipeline components and add them to the pipeline
    # nlp.create_pipe works for built-ins that are registered with spaCy
    if 'ner' not in nlp.pipe_names:
        ner = nlp.create_pipe('ner')
        nlp.add_pipe(ner, last=True)

    # otherwise, get it so we can add labels
    else:
        ner = nlp.get_pipe("ner")

    # add labels
    for _, annotations in Train_data:
         for ent in annotations.get('entities'):
            ner.add_label(ent[2])
            
    #for i in my_ent:
     #   ner.add_label(i)

    # get names of other pipes to disable them during training
    #other_pipes = [pipe for pipe in nlp.pipe_names if pipe != 'ner']
    #with nlp.disable_pipes(*other_pipes):  # only train NER
        # reset and initialize the weights randomly – but only if we're
        # training a new model
    if model is None:
        optimize=nlp.begin_training()
    else:
        optimize= nlp.resume_training()
    #if model is None:
     #   optimizer = nlp.begin_training()
    #else:
     #   optimizer = nlp.entity.create_optimizer()
    
    other_pipes = [pipe for pipe in nlp.pipe_names if pipe != 'ner']
    with nlp.disable_pipes(*other_pipes):  # only train NER

        for itn in range(n_iter):
            print("Starting iteration" + str(itn))
            random.shuffle(Train_data)
            losses = {}
            # batch up the examples using spaCy's minibatch
            batches = minibatch(Train_data, size=compounding(4.0, 32.0, 1.001))
            for batch in batches:
                texts, annotations = zip(*batch)
                nlp.update(
                texts,  # batch of texts
                annotations,  # batch of annotations
                sgd= optimize,
                drop=0.2,  # dropout - make it harder to memorise data
                losses=losses,
                )
                
            print("Losses", losses)
    new_model=nlp
    # test the trained model
    for text, _ in Train_data:
        doc = nlp(text)
        print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
        print("Tokens", [(t.text, t.ent_type_, t.ent_iob) for t in doc])
        displacy.render(doc, jupyter=True, style='ent')
        
    # save model to output directory
    #if output_dir2 is not None:
     #   output_dir2 = Path(output_dir2)
      #  if not output_dir2.exists():
       #     output_dir2.mkdir()
    nlp.to_disk(output_dir2)
    print("Saved model to", output_dir2)
main_train(model=None, output_dir=r'model', n_iter=300)

Created blank 'en' model
Starting iteration0
Losses {'ner': 746.7716024898473}
Starting iteration1
Losses {'ner': 400.7020986160496}
Starting iteration2
Losses {'ner': 310.18514683819376}
Starting iteration3
Losses {'ner': 231.94757369030413}
Starting iteration4
Losses {'ner': 294.9199534156651}
Starting iteration5
Losses {'ner': 310.44326214847024}
Starting iteration6
Losses {'ner': 282.70629219436523}
Starting iteration7
Losses {'ner': 323.5448618080409}
Starting iteration8
Losses {'ner': 295.49561572460516}
Starting iteration9
Losses {'ner': 325.99492600994563}
Starting iteration10
Losses {'ner': 275.0109681750025}
Starting iteration11
Losses {'ner': 302.3306911237687}
Starting iteration12
Losses {'ner': 220.1438017102755}
Starting iteration13
Losses {'ner': 193.90910567974606}
Starting iteration14
Losses {'ner': 180.0542070528165}
Starting iteration15
Losses {'ner': 168.73334594786138}
Starting iteration16
Losses {'ner': 137.4121194747734}
Starting iteration17
Losses {'ner': 129.96

Entities [('in the centre of town', 'taxi-destination')]
Tokens [('We', '', 2), ('do', '', 2), ("n't", '', 2), ('have', '', 2), ('any', '', 2), ('multiple', '', 2), ('sports', '', 2), ('facilities', '', 2), ('in', 'taxi-destination', 3), ('the', 'taxi-destination', 1), ('centre', 'taxi-destination', 1), ('of', 'taxi-destination', 1), ('town', 'taxi-destination', 1), ('.', '', 2), ('Do', '', 2), ('you', '', 2), ('want', '', 2), ('to', '', 2), ('look', '', 2), ('for', '', 2), ('something', '', 2), ('else', '', 2), ('?', '', 2)]


Entities [('colleges', 'attraction-type'), ('in the centre', 'attraction-area'), ("King's College", 'attraction-name'), ("Saint Catharine's College", 'attraction-name')]
Tokens [('There', '', 2), ('are', '', 2), ('13', '', 2), ('colleges', 'attraction-type', 3), ('in', 'attraction-area', 3), ('the', 'attraction-area', 1), ('centre', 'attraction-area', 1), ('.', '', 2), (' ', '', 2), ('King', 'attraction-name', 3), ("'s", 'attraction-name', 1), ('College', 'attraction-name', 1), ('and', '', 2), ('Saint', 'attraction-name', 3), ('Catharine', 'attraction-name', 1), ("'s", 'attraction-name', 1), ('College', 'attraction-name', 1), ('are', '', 2), ('on', '', 2), ('the', '', 2), ('same', '', 2), ('street', '', 2), ('and', '', 2), ('both', '', 2), ('have', '', 2), ('free', '', 2), ('admission', '', 2), ('.', '', 2)]


Entities [('cheap place', 'hotel-price-range'), ('in the center', 'hotel-area')]
Tokens [('Thanks', '', 2), ('.', '', 2), ('I', '', 2), ('also', '', 2), ('need', '', 2), ('a', '', 2), ('cheap', 'hotel-price-range', 3), ('place', 'hotel-price-range', 1), ('to', '', 2), ('stay', '', 2), ('in', 'hotel-area', 3), ('the', 'hotel-area', 1), ('center', 'hotel-area', 1), ('.', '', 2)]


Entities [('from Cambridge', 'train-departure'), ('on Tuesday', 'train-day'), ('to Leicester', 'train-destination'), ('by 18:00', 'train-arrive-by')]
Tokens [('I', '', 2), ("'ll", '', 2), ('be', '', 2), ('leaving', '', 2), ('from', 'train-departure', 3), ('Cambridge', 'train-departure', 1), ('on', 'train-day', 3), ('Tuesday', 'train-day', 1), ('.', '', 2), ('I', '', 2), ("'d", '', 2), ('like', '', 2), ('to', '', 2), ('get', '', 2), ('to', 'train-destination', 3), ('Leicester', 'train-destination', 1), ('by', 'train-arrive-by', 3), ('18:00', 'train-arrive-by', 1), ('please', '', 2), ('.', '', 2)]


...

Entities [('the gonville hotel', 'hotel-name'), ('expensive', 'hotel-price-range')]
Tokens [('I', '', 2), ('have', '', 2), ('the', 'hotel-name', 3), ('gonville', 'hotel-name', 1), ('hotel', 'hotel-name', 1), ('.', '', 2), ('It', '', 2), ('is', '', 2), ('expensive', 'hotel-price-range', 3), ('.', '', 2), ('Would', '', 2), ('you', '', 2), ('like', '', 2), ('me', '', 2), ('to', '', 2), ('book', '', 2), ('that', '', 2), ('for', '', 2), ('you', '', 2), ('?', '', 2)]


Entities [('The allenbell', 'hotel-name'), ('guesthouse', 'hotel-type'), ('in the east', 'hotel-area'), ('cheap 4 star', 'hotel-stars'), ('free parking', 'hotel-parking')]
Tokens [('The', 'hotel-name', 3), ('allenbell', 'hotel-name', 1), ('is', '', 2), ('a', '', 2), ('guesthouse', 'hotel-type', 3), ('located', '', 2), ('in', 'hotel-area', 3), ('the', 'hotel-area', 1), ('east', 'hotel-area', 1), ('.', '', 2), ('It', '', 2), ('is', '', 2), ('a', '', 2), ('cheap', 'hotel-stars', 3), ('4', 'hotel-stars', 1), ('star', 'hotel-stars', 1), ('hotel', '', 2), ('with', '', 2), ('free', 'hotel-parking', 3), ('parking', 'hotel-parking', 1), ('and', '', 2), ('internet', '', 2), ('.', '', 2)]


Entities [('cheap', 'restaurant-price-range'), ('Spanish cuisine', 'restaurant-food')]
Tokens [('I', '', 2), ('recommend', '', 2), ('La', '', 2), ('Raza', '', 2), ('-', '', 2), ('fantastic', '', 2), ('(', '', 2), ('and', '', 2), ('cheap', 'restaurant-price-range', 3), ('!', '', 2), (')', '', 2), ('Spanish', 'restaurant-food', 3), ('cuisine', 'restaurant-food', 1), ('.', '', 2), ('I', '', 2), ("'d", '', 2), ('be', '', 2), ('happy', '', 2), ('to', '', 2), ('book', '', 2), ('a', '', 2), ('table', '', 2), ('for', '', 2), ('you', '', 2), (',', '', 2), ('if', '', 2), ('you', '', 2), ('like', '', 2), ('.', '', 2)]


Entities [('from broxbourne', 'train-departure'), ('at 21:01', 'train-leave-at')]
Tokens [('Actually', '', 2), ('yes', '', 2), ('!', '', 2), ('TR5975', '', 2), ('leaves', '', 2), ('from', 'train-departure', 3), ('broxbourne', 'train-departure', 1), ('at', 'train-leave-at', 3), ('21:01', 'train-leave-at', 1), ('.', '', 2), ('It', '', 2), ("'s", '', 2), ('14.32', '', 2), ('pounds', '', 2), ('.', '', 2), ('Does', '', 2), ('that', '', 2), ('work', '', 2), ('?', '', 2)]


Saved model to output_dir2


### Testing the model

In [8]:
def test_model(nlp):
    texts = [
        "I'm looking for a 4 star hotel.",
        "I've found 21 4 star hotels. Is there a certain area you want to stay in?",
        "Yes, in the east, please.",
        "I have found several hotels. Do you have any preference towards price?",
        "I would not mind finding one with free wifi.",
        "Unfortunately, we don't have any hotels with those preference in the area, but we do have 6 guesthouses available. Would a guesthouse be okay?",
        "A guesthouse is fine. Which one would you recommend?",
        "I recommend the Leverton House. It's a cheap guesthouse, but still a 4-star establishment.",
        "That sounds good.  Can you give me the address and postcode for Leverton House?",
        "They are located at 732-734 newmarket road, and postcode is cb58rs",
        "Thank you. I'm also looking for a venetian restaurant on the east side as well.", 
        "I'm sorry there are no Venetian restaurants. Are there any cuisines I can look for?",
        "Yes, how about one that serves Indian food?",
        "There are four restaurants that serve indian food in the east. Do you have a price range?",
        "Book one of them for 8 people at 14:15 on tuesday.",
        "Alright, I have you booked at Curry Prince. Your reference number is: 55UNFF8Z. Anything else I can do for you today?",
        "Yes, can you schedule a taxi to take me from Leverton House to Curry Prince? I need to get there by 14:15. ",
        "Okay, your taxi car type is a white bmw and the contact number is 07967879848. Is there anything else you need?",
        "That is all.  Thank you",
        "Yes I would like to book the train for 4 people and I'll need the reference number please.",
        "I've got three that fit that bill... the gardenia, la mimosa, and shiraz.  Do you have a preference?",
        "Great, could I book a table of 5 for 11:30 on wednesday?",
    ]
    print("Loading from", output_dir2)
    nlp2 = spacy.load(output_dir2)
    docs = nlp2.pipe(texts)
    for doc in docs:
        print(doc.text)
        print([(t.text, t.dep_, t.head.text) for t in doc if t.dep_ != "-"])
        displacy.render(doc, jupyter=True, style='ent')

In [9]:
test_model(nlp)

Loading from output_dir2
I'm looking for a 4 star hotel.
[('I', '', 'I'), ("'m", '', "'m"), ('looking', '', 'looking'), ('for', '', 'for'), ('a', '', 'a'), ('4', '', '4'), ('star', '', 'star'), ('hotel', '', 'hotel'), ('.', '', '.')]


I've found 21 4 star hotels. Is there a certain area you want to stay in?
[('I', '', 'I'), ("'ve", '', "'ve"), ('found', '', 'found'), ('21', '', '21'), ('4', '', '4'), ('star', '', 'star'), ('hotels', '', 'hotels'), ('.', '', '.'), ('Is', '', 'Is'), ('there', '', 'there'), ('a', '', 'a'), ('certain', '', 'certain'), ('area', '', 'area'), ('you', '', 'you'), ('want', '', 'want'), ('to', '', 'to'), ('stay', '', 'stay'), ('in', '', 'in'), ('?', '', '?')]


Yes, in the east, please.
[('Yes', '', 'Yes'), (',', '', ','), ('in', '', 'in'), ('the', '', 'the'), ('east', '', 'east'), (',', '', ','), ('please', '', 'please'), ('.', '', '.')]


I have found several hotels. Do you have any preference towards price?
[('I', '', 'I'), ('have', '', 'have'), ('found', '', 'found'), ('several', '', 'several'), ('hotels', '', 'hotels'), ('.', '', '.'), ('Do', '', 'Do'), ('you', '', 'you'), ('have', '', 'have'), ('any', '', 'any'), ('preference', '', 'preference'), ('towards', '', 'towards'), ('price', '', 'price'), ('?', '', '?')]


/usr/lib/python3.5/runpy.py:184: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  "__main__", mod_spec)


...

That is all.  Thank you
[('That', '', 'That'), ('is', '', 'is'), ('all', '', 'all'), ('.', '', '.'), (' ', '', ' '), ('Thank', '', 'Thank'), ('you', '', 'you')]


/usr/lib/python3.5/runpy.py:184: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  "__main__", mod_spec)


Yes I would like to book the train for 4 people and I'll need the reference number please.
[('Yes', '', 'Yes'), ('I', '', 'I'), ('would', '', 'would'), ('like', '', 'like'), ('to', '', 'to'), ('book', '', 'book'), ('the', '', 'the'), ('train', '', 'train'), ('for', '', 'for'), ('4', '', '4'), ('people', '', 'people'), ('and', '', 'and'), ('I', '', 'I'), ("'ll", '', "'ll"), ('need', '', 'need'), ('the', '', 'the'), ('reference', '', 'reference'), ('number', '', 'number'), ('please', '', 'please'), ('.', '', '.')]


I've got three that fit that bill... the gardenia, la mimosa, and shiraz.  Do you have a preference?
[('I', '', 'I'), ("'ve", '', "'ve"), ('got', '', 'got'), ('three', '', 'three'), ('that', '', 'that'), ('fit', '', 'fit'), ('that', '', 'that'), ('bill', '', 'bill'), ('...', '', '...'), ('the', '', 'the'), ('gardenia', '', 'gardenia'), (',', '', ','), ('la', '', 'la'), ('mimosa', '', 'mimosa'), (',', '', ','), ('and', '', 'and'), ('shiraz', '', 'shiraz'), ('.', '', '.'), (' ', '', ' '), ('Do', '', 'Do'), ('you', '', 'you'), ('have', '', 'have'), ('a', '', 'a'), ('preference', '', 'preference'), ('?', '', '?')]


Great, could I book a table of 5 for 11:30 on wednesday?
[('Great', '', 'Great'), (',', '', ','), ('could', '', 'could'), ('I', '', 'I'), ('book', '', 'book'), ('a', '', 'a'), ('table', '', 'table'), ('of', '', 'of'), ('5', '', '5'), ('for', '', 'for'), ('11:30', '', '11:30'), ('on', '', 'on'), ('wednesday', '', 'wednesday'), ('?', '', '?')]


In [10]:
print("Loading from", output_dir2)
nlp2 = spacy.load(output_dir2)
doc = nlp2("3 nights, 3 people, please.")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
displacy.render(doc,  style='ent')

Loading from output_dir2
Entities [('3 nights', 'hotel-book-stay'), ('3 people', 'hotel-book-people')]


In [11]:
print("Loading from", output_dir2)
nlp2 = spacy.load(output_dir2)
doc = nlp2("Do they have free parking? If so, please reserve a room for Tuesday for 7 people, 4 nights.")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
displacy.render(doc,  style='ent')

Loading from output_dir2
Entities [('free parking', 'hotel-parking'), ('for Tuesday', 'hotel-book-day'), ('for 7 people', 'hotel-book-people'), ('4 nights', 'hotel-book-stay')]


In [12]:
print("Loading from", output_dir2)
nlp2 = spacy.load(output_dir2)
doc = nlp2("I want to reserve a room for 4 nights.")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
displacy.render(doc,  style='ent')

Loading from output_dir2
Entities [('for 4', 'hotel-book-day'), ('nights.', 'hotel-book-people')]


In [13]:
print("Loading from", output_dir2)
nlp2 = spacy.load(output_dir2)
doc = nlp2("Hello, I am looking for some places to go in the centre of town. There is a lot to do in the centre. Is there a certain type of attraction you'd like to see or do? I was thinking something related to multiple sports We don't have any multiple sports facilities in the centre of town. Do you want to look for something else? How about a theatre? I think we would enjoy seeing a show! May I recommend Cambridge Arts Theatre located in the centre of town? That would be great. Can I have the postcode, address, and entrance fee please? I don't have any information about admission, but you can call them to get more information.  The number is 01223503333. The address is 6 saint edward's passage cb23pj Ok.  I also need info on the restaurant Darrys cookhouse and wine shop. Darrys Cookhouse and Wine Shop is a modern European restaurant located in the centre of town.  It's in the expensive price range.  Would you like to make a reservation? Yes, that would be great. I'll need a table for 7 on Friday at 18:00.  Booking was successful. The table will be reserved for 15 minutes. Reference number is : BT75ESXM. Can I help you with anything else? I don't think so.  Thanks for all your help. Hope you have a great time during your trip. That was so nice of you to say thanks so much. You're very welcome! Take care!")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
displacy.render(doc,  style='ent')

Loading from output_dir2
Entities [('some places', 'restaurant-price-range'), ('in the centre', 'hotel-area'), ('in the centre of town', 'attraction-area'), ('show!', 'attraction-name'), ('Cambridge Arts Theatre', 'hotel-price-range'), ('in the centre', 'hotel-area'), ('cookhouse and wine', 'train-destination'), ('Wine Shop', 'restaurant-name'), ('modern European', 'restaurant-food'), ('in the centre', 'restaurant-area'), ('expensive', 'restaurant-price-range'), ('a table for 7', 'restaurant-book-people'), ('on Friday', 'restaurant-book-day'), ('at 18:00.', 'restaurant-book-time'), ('Booking was successful', 'attraction-name'), ('The table', 'hotel-name'), ('for 15', 'hotel-book-day'), ('minutes', 'hotel-price-range'), ('welcome', 'restaurant-price-range')]


In [14]:
print("Loading from", output_dir2)
nlp2 = spacy.load(output_dir2)
doc = nlp2("I am looking for the addresses of each of the moderately priced restaurants in the south part of town. The address for Pizza Hut Cherry Hinton is G4 Cambridge Leisure Park Clifton Way Cherry Hinton and the address for Restaurant Alimentum is 152 - 154 Hills Road. Is there anything else? There is restaurant alimentum which is a modern european restaurant located in the south part of town and is in the moderate price range. Could you give me the address for Restaurant Alimentum? Restaurant Alimentum's address is G4 Cambridge Leisure Park Clifton Way Cherry Hinton. May I help you with anything else? No thank you good bye Thank you for using our system. Goodbye.")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
displacy.render(doc,  style='ent')

Loading from output_dir2
Entities [('in the south part of town', 'restaurant-area'), ('Pizza Hut', 'restaurant-food'), ('Hinton is', 'train-departure'), ('G4 Cambridge', 'hotel-type'), ('Leisure Park', 'train-day'), ('Cherry Hinton', 'restaurant-name'), ('for Restaurant', 'restaurant-food'), ('Alimentum is', 'restaurant-price-range'), ('Hills Road', 'hotel-price-range'), ('alimentum which', 'taxi-leave-at'), ('modern european', 'restaurant-food'), ('in the south', 'restaurant-area'), ('Park Clifton Way Cherry Hinton', 'restaurant-area')]


### Model evaluation

In [ ]:
def evaluate(model, examples):
    scorer = Scorer()
    for text, metadata in Train_data:
        #print(text)
        doc_gold_text = model.make_doc(text)
        gold = GoldParse(doc_gold_text, entities=metadata['entities'])
        pred_value = model(text)
        scorer.score(pred_value, gold)
        print(scorer.score(pred_value, gold))
    return scorer.scores

test_result = evaluate(new_model, Train_data)

In [ ]:
new_sentence=""
result1= open("FinalData/chatito/chatito_data.txt","w+")
result2= open("FinalData/chatette/chatette_data.txt","w+")
r1 = open("FinalData/chatito/chatito_data.txt", "r+")  
r2 = open("FinalData/chatette/chatette_data.txt", "r+")
r1.write("\n")
r2.write("\n")
for object_1 in dict_json_weighted: 
    for i in range(len(dict_json_weighted[object_1]['log'])):
        print(str(i)+"-"+dict_json_weighted[object_1]['log'][i]['text'])
        sentence =nlp2 (dict_json_weighted[object_1]['log'][i]['text'])
        ### create a file for each sentence in both directories 

        ### print the label
        #print("Verbs:", [token.lemma_ for token in sentence if token.pos_ == "VERB"])
        r1 = open("FinalData/chatito/chatito_data.txt", "r+")  
        r2 = open("FinalData/chatette/chatette_data.txt", "r+")

        for X in (sentence.ents) :
            print([(X.text, X.label_) ])

            r1 = open("FinalData/chatito/chatito_data.txt", "r+")  
            r2 = open("FinalData/chatette/chatette_data.txt", "r+")

                #using chatette format
            if X.label_ in r2.read():
                r2.write("|"+X.text)
            else:
                r2.write("\n")
                r2.write("\n")
                r2.write(" ~["+X.label_+"]\n")
                r2.write("   "+X.text)
                 #using chatito format
            if X.label_ in r1.read():
                r1.write("   "+X.text+"\n")
            else: 
                r1.write("\n")
                r1.write("\n")
                r1.write("~["+X.label_+"]\n")
                r1.write("   "+X.text+"\n")


        ### highlight named entities and their labels in a text
        displacy.render(sentence, jupyter=True, style='ent')



0-Yes, I'd like some help looking for a particular restaurant. The name of the restaurant is Darrys Cookhouse and Wine Shop. I'd like to know where it's located and how expensive.
[('a particular', 'hotel-stars')]
[('The name', 'hotel-book-stay')]
[('Darrys Cookhouse and Wine Shop', 'restaurant-name')]


1-Certainly it is in the expensive price range and it is located at 40270 King Street City Center.
[('Certainly it', 'restaurant-name')]
[('expensive', 'attraction-type')]
[('40270 King', 'hotel-stars')]
[('Street City Center', 'hotel-price-range')]


2-Perfect, could you make a reservation for 7 people at 17:00 on Sunday?
[('for 7 people', 'hotel-book-people')]
[('at 17:00', 'restaurant-book-time')]
[('on Sunday', 'restaurant-bookday')]


3-Unfortunately there are no reservations available at that time. Would you like me to look for another restaurant?


/usr/lib/python3.5/runpy.py:184: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  "__main__", mod_spec)


...

12-I do not have one in mind, no.


/usr/lib/python3.5/runpy.py:184: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  "__main__", mod_spec)


13-There is a train leaving from Ely at 09:35 and arriving in Cambridge at 09:52. How does that sound? 
[('at 09:35', 'train-leave-at')]
[('in Cambridge at', 'restaurant-area')]
[('09:52. How does', 'attraction-area')]


14-That would be great. Can you get me 8 tickets on that train, and give me the reference number?
[('8 tickets', 'train-book-people')]
[('give', 'attraction-type')]


15-I have booked your order, your total is 28.16
